# Assignment 6 Part Two: FineTuning Bert


### Instructions
- Do **NOT** forget to type in your name and AUBNET After this cell.
- Do **NOT** upload the dataset with your submission.
- Name the assignment as follows: **Ast6_p2_AUBNET.ipynb** . Failure to follow this naming convention will result in the notebook **not being graded**.

**Note:**
<div class="alert alert-danger" role="alert">
   <b>This notebook will be reviewed to ensure the work is original and not generated by AI. If any part of the submission is found to be AI-generated, it may result in a grade of zero for the entire assignment.</b><br>
   <b>We appreciate your effort in submitting authentic work and encourage you to reach out if you have any questions.</b>
</div>

In [ ]:
aub_net="rmm85"
name="Ralph Mouawad"

Recommended Readings
- [BERT: Pre-training of Deep Bidirectional Transformers for Language Understanding](https://arxiv.org/abs/1810.04805) Jacob Devlin, Ming-Wei Chang, Kenton Lee, Kristina Toutanova. NAACL 2019.
- [Generalized Language Models](https://lilianweng.github.io/posts/2019-01-31-lm/) Lillian Weng. 2019
- [The Illustrated BERT, ELMo, and co. (How NLP Cracked Transfer Learning)](http://jalammar.github.io/illustrated-bert/) Jay Alammar. 2019



# Introduction to HuggingFace Transformers

This homework focuses on the HuggingFace transformers library, a crucial tool for professionals working with Natural Language Processing (NLP) technology. The library enables downloading, running, and training language models with ease.

You'll need to install four key HuggingFace libraries:

1. Transformers (`!pip install transformers`): Handles model inference
2. Accelerate (`!pip install accelerate`): Supports model training
3. Datasets (`!pip install datasets`): Assists with data processing
4. Evaluate (`!pip install evaluate`): Facilitates model evaluation

In [1]:
%%shell
pip install datasets
pip install transformers
pip install --upgrade accelerate
pip install evaluate

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 16.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 9.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 13.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 8.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 13.3 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 336.4/336.4 kB 14.6 MB/s eta 0:00:00
  Attempting uninstall: accelerate
    Found existing installation: accelerate 1.

In [2]:
from transformers import pipeline
from transformers import AutoTokenizer, AutoModelForSequenceClassification, AutoModelForTokenClassification
from transformers import Trainer, TrainingArguments, DataCollatorForLanguageModeling
import datasets
from datasets import load_dataset#, list_datasets
from evaluate import evaluator
import evaluate
import numpy as np
import torch
import copy

from collections import defaultdict

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device_id = 0 if str(device) == 'cuda' else -1

In [3]:
print(device_id)

0


# Part 1: Zero-Shot Learning with Pre-Trained Language Models


We'll be utilizing BERT, a groundbreaking pre-trained language model introduced in late 2018 through the research paper "BERT: Pre-training of Deep Bidirectional Transformers for Language Understanding".

BERT was trained using Masked Language Modeling, a technique where the model learns to predict masked words in input sequences. For instance, in a sample sentence, BERT might have an 84.7% probability of correctly identifying "Italian" as the masked word.

The model leverages bidirectional context understanding, allowing it to comprehend word meanings based on surrounding text in both forward and backward directions. This approach enables more nuanced and contextually accurate language processing compared to previous unidirectional models.

[BERT](https://arxiv.org/abs/1810.04805)

In [4]:
# Download and query the bert-base-cased model
bert_model = pipeline('fill-mask', model='bert-base-cased', device=device_id)
print(bert_model("I went to an [MASK] restaurant and ordered pasta."))

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/436M [00:00<?, ?B/s]

BertForMaskedLM has generative capabilities, as `prepare_inputs_for_generation` is explicitly overwritten. However, it doesn't directly inherit from `GenerationMixin`. From 👉v4.50👈 onwards, `PreTrainedModel` will NOT inherit from `GenerationMixin`, and this model will lose the ability to call `generate` and other related functions.
  - If you're using `trust_remote_code=True`, you can get rid of this warning by loading the model with an auto class. See https://huggingface.co/docs/transformers/en/model_doc/auto#auto-classes
  - If you are the owner of the model architecture code, please modify your model class such that it inherits from `GenerationMixin` (after `PreTrainedModel`, otherwise you'll get an exception).
  - If you are not the owner of the model architecture class, please contact the model code owner to update it.
Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls

tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/213k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/436k [00:00<?, ?B/s]

[{'score': 0.8473308086395264, 'token': 2169, 'token_str': 'Italian', 'sequence': 'I went to an Italian restaurant and ordered pasta.'}, {'score': 0.03583093360066414, 'token': 1890, 'token_str': 'Indian', 'sequence': 'I went to an Indian restaurant and ordered pasta.'}, {'score': 0.016542408615350723, 'token': 1385, 'token_str': 'old', 'sequence': 'I went to an old restaurant and ordered pasta.'}, {'score': 0.006616922095417976, 'token': 3427, 'token_str': 'empty', 'sequence': 'I went to an empty restaurant and ordered pasta.'}, {'score': 0.005878509022295475, 'token': 6210, 'token_str': 'Egyptian', 'sequence': 'I went to an Egyptian restaurant and ordered pasta.'}]


BERT's versatility allows it to potentially tackle various natural language processing tasks by creatively framing them as fill-in-the-blank problems. This includes complex challenges like Question Answering, Language Identification, Part-of-Speech Tagging, and even Translation, all by strategically structuring input prompts to leverage the model's contextual understanding.

In [5]:
# Language Identification
print(bert_model("I am currently speaking in the [MASK] language.")[0])

# Factual QA
print(bert_model("The Declaration of Independence was written in the year [MASK].")[0])

# Part of speech tagging
print(bert_model("The word run is a [MASK].")[0])

# Translation
print(bert_model("The French word amour translates to [MASK] in English.")[0])

{'score': 0.18785135447978973, 'token': 1483, 'token_str': 'English', 'sequence': 'I am currently speaking in the English language.'}
{'score': 0.10682458430528641, 'token': 14447, 'token_str': '1776', 'sequence': 'The Declaration of Independence was written in the year 1776.'}
{'score': 0.22859828174114227, 'token': 12464, 'token_str': 'verb', 'sequence': 'The word run is a verb.'}
{'score': 0.055166736245155334, 'token': 1567, 'token_str': 'love', 'sequence': 'The French word amour translates to love in English.'}


Contrary to initial expectations, BERT struggles to perform well on complex natural language tasks without additional training. In the part1, we'll first assess BERT's baseline performance on sentiment analysis to understand its raw capabilities. Subsequently, we'll implement targeted training to demonstrate how model performance can be significantly improved through fine-tuning.

In [6]:
# Language Identification (failed)
print(bert_model("今[MASK]で話しています")[0])

# Factual QA (failed)
print(bert_model("The U.S.A. was founded in the year [MASK].")[0])

# Part of speech tagging (failed)
print(bert_model("The word golf is a [MASK].")[0])

# Translation (failed)
print(bert_model("The French word bonjour translates to [MASK] in English.")[0])

{'score': 0.5789163708686829, 'token': 100, 'token_str': '[UNK]', 'sequence': 'しています'}
{'score': 0.1736524999141693, 'token': 1196, 'token_str': 'before', 'sequence': 'The U. S. A. was founded in the year before.'}
{'score': 0.15804286301136017, 'token': 8155, 'token_str': 'joke', 'sequence': 'The word golf is a joke.'}
{'score': 0.016320660710334778, 'token': 6164, 'token_str': 'wolf', 'sequence': 'The French word bonjour translates to wolf in English.'}


### **Sequence Classification with pre-trained BERT**

In this section we'll be evaluating BERT for sentiment analysis without fine-tuning. This is purely for the purposes of demonstration as you'll
This section demonstrates BERT's sentiment analysis capabilities without fine-tuning, highlighting the model's initial performance before targeted training.
To perform sequence classification without fine-tuning, two key elements are required:

A mask-filling template appended to the sequence
A set of `target` class labels

For example, given the sentence "I just saw a movie today and it was really great", BERT predicts a 2.78% chance of the `[MASK]` token being "positive" and a 1.65% chance of being "negative", resulting in a positive classification.

In [7]:
bert_model("I just saw a movie today and it was really great. My opinion of the movie is [MASK].", targets=["positive", "negative"])

[{'score': 0.027819881215691566,
  'token': 3112,
  'token_str': 'positive',
  'sequence': 'I just saw a movie today and it was really great. My opinion of the movie is positive.'},
 {'score': 0.01648259349167347,
  'token': 4366,
  'token_str': 'negative',
  'sequence': 'I just saw a movie today and it was really great. My opinion of the movie is negative.'}]

We'll evaluate BERT's sentiment analysis capabilities using the Yelp Reviews dataset, which contains 650,000 reviews with user-assigned star ratings. The challenge is to predict the number of stars (ranging from 1 to 5) based solely on the review's text content.

In [8]:
# Download the yelp dataset from huggingface
dataset = load_dataset("yelp_review_full")

README.md:   0%|          | 0.00/6.72k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/299M [00:00<?, ?B/s]

test-00000-of-00001.parquet:   0%|          | 0.00/23.5M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/650000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/50000 [00:00<?, ? examples/s]

### **Dataset Processing**

HuggingFace's `Map` function is powerful for dataset manipulation. It applies a function `f` to every dataset row, allowing column creation or modification. Two equivalent methods for creating a reverse label column are:

```python
def reverse_label(row):
  return {'reverse_label': int(not row["binary_label"])}

def reverse_label(row):
  row['reverse_label'] = int(not row["binary_label"])
  return row
```

Use `dataset.map(reverse_label)` to apply the transformation.

### **Concatenating the Mask-Fill Template**

Task: Add a new `input` column by concatenating a mask-fill template to each `text` column entry. Refer to the `Map` function documentation for guidance on implementation.

In [17]:
def concatenate_mask(row):
  #Concatenate the template to each example and return in a new column "input"
  template = " I give it a score of [MASK] out of 5."
  ### YOUR CODE STARTS HERE ###
  row['input']= row['text']+ template # every text now has the template next to it so we can evaluate the score predictions
  ### YOUR CODE ENDS HERE ###
  return row

test_data = dataset['test'].map(concatenate_mask)

### Introduction to BERT Tokenization


Language models like BERT require text to be broken down into tokens before processing. Due to its Transformer architecture, BERT has a strict 512-token limit. Attempting to input a text sequence longer than this maximum will trigger an error, preventing model analysis of extensive texts.

In [18]:
# Giving BERT a piece of text with more than 512 tokens produces an error
try:
  bert_model("Hello " * 512 + " my name is [MASK]")
except RuntimeError as e:
  print(e)

The size of tensor a (518) must match the size of tensor b (512) at non-singleton dimension 1


### **Filtering Dataset for BERT's Maximum Token Length**

The BERT tokenizer converts text into tokens, returning a dictionary with `input_ids`, `attention_mask`, and `token_type_ids`. To ensure compatibility with BERT's architecture, filter the dataset to include only examples with 512 or fewer tokens.

Use the `Filter` function, which keeps rows where the condition returns `True`. Leverage `tokenizer.model_max_length` to dynamically set the maximum sequence length, avoiding hard-coded numbers.

In [34]:
tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")

def filter_for_max_length(row):
  # Return True if the length of the input (in tokens) is less than or equal
  # to the maximum length allowed by the BERT model
  ## YOUR CODE STARTS HERE ###

  # tokens = tokenizer.tokenize(row['input'], truncation=False) #convert the input texts into tokens so we compare the length for BERT requirements
  tokens=tokenizer(row['input'],truncation=False) ## I used this method as it returns the list of input IDs and takes into consideration the CLS and SEP tokens
  # which is required when I filter the sentence
  # if len(tokens) >= tokenizer.model_max_length:

  if len(tokens['input_ids']) >= tokenizer.model_max_length: # I check the length pf the dict containing the token IDs to see if it is the right size
    return False ## I used this method bcz the previous was returning 0.19 later on instead of 0.24 bcz special tokens were not taken into consideration
  ### YOUR CODE ENDS HERE ###

  return True

filtered_data = test_data.filter(filter_for_max_length)

Filter:   0%|          | 0/50000 [00:00<?, ? examples/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (802 > 512). Running this sequence through the model will result in indexing errors


In [38]:
print(filtered_data)

Dataset({
    features: ['label', 'text', 'input'],
    num_rows: 47246
})


We'll randomly select 100 examples from the filtered dataset for testing. This sampling approach helps manage runtime while providing a representative subset. In an ideal scenario with unlimited time, using the full dataset would be preferable.

In [39]:
# Randomly sample 100 examples from the dataset (do not change!)
sampled_data = filtered_data.shuffle(seed=42).select(range(100))

### **Applying BERT for Star Rating Prediction**

Create a function to process each text sequence in the dataset's `input` column. The function should use BERT to predict the most likely star rating (1-5) and add this prediction to a new `score` column. Utilize the `targets` field to specify the possible ratings `[1, 2, 3, 4, 5]`, referring to previous section guidelines for implementation.

In [40]:
def apply_bert(row):
  # Compute the probabilities for each score and return the value of the most likely score
  ## YOUR CODE STARTS HERE ###
  # process the input
  bert_inp=row['input'] #extract the input text that BERT will analyze
  bert_targets=['1','2', '3','4', '5'] # the targets we're looking for
  bert_pred= bert_model(bert_inp, targets=bert_targets) # we will have a list of predictions with the corresponding scores
  prediction=max(bert_pred,key=lambda x:x['score']) # take the prediction with highest score

  ### we still need to get the score
  score=prediction['token_str'] # retrieve the prediction from what we retrieved earlier
  ### YOUR CODE ENDS HERE ###
  return {'score': int(score)}

predicted_data = sampled_data.map(apply_bert)

Map:   0%|          | 0/100 [00:00<?, ? examples/s]

In [41]:
print(predicted_data['score'])

[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 2, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 2, 4, 4, 4, 4, 4, 4, 4, 4, 2, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]


### **Model Performance Evaluation**

The model's accuracy should hover around 24% - marginally better than random chance for a five-class classification task. This low performance demonstrates BERT's inability to perform sentiment analysis without specialized training, underscoring the necessity of fine-tuning to improve predictive capabilities.

NOTE:

The method I used first for filtering gave me an acc of 0.19. The second one gave me 0.28 which I'll stick to.

In [43]:
def accuracy(outputs, reference):
  return sum([o == r for o, r in zip(outputs, reference)]) / len(reference)

print(accuracy(predicted_data["score"], predicted_data["label"]))

0.28


# Part 2: Training BERT for Sentiment Analysis


In this section we'll be training BERT for the same Sentiment Analysis task from Section 1. We'll start by giving a short introduction to the concept of fine-tuning.

### **What is fine-tuning?**

Fine-tuning is the process of further training a pre-trained model to accomplish a particular down-stream task. This is typically done by swapping out the pre-trained model's last layer (its head) for a new randomly initialized head and training both model and head.

### **Model "heads"**

The final output layer of a language model is typically called a "head". The standard head used by models when pre-training is called a "languge modeling head". This is a dense linear layer that projects the $D_{enc}$ length encodings of each of the $L_{context}$ tokens to a probability distribution over the vocabulary. The total size of this layer is thus ($L_{context} * D_{enc}$ x $|V|$).
<!-- The head and the network are always trained *together*. We compute the cross-entropy loss $L = -\log(P(w))$ using the output of the head and backpropagate through the head to the rest of the network. -->

### **Adding on a "Classification head"**

In Section 1 we used BERT's language modeling head to perform the Sentiment Analysis task. While we *can* train the model with its original LM head, this is unnecessary, as the LM head outputs probabilities over all tokens rather than just our targets. Thus, in this section we're going to remove the language modeling head and replace it with a classification head.

A classification head is very similar to a language modeling head. It is a dense linear layer that projects the $D_{enc}$ length encodings of each of the $L_{context}$ tokens to a probability distribution over the *$n$ classes* rather than the whole vocabulary. The total size of this layer is thus ($L_{context} * D_{enc}$ x $n$). This makes it significantly more efficient to train.

### **Using HuggingFace to swap heads**

Loading a model with a particular head is easy using HuggingFace. All you do is load the model as an instance of a given class. The classes we're using in this homework are as follows:
1. [AutoModelForMaskedLM](https://huggingface.co/docs/transformers/model_doc/auto#transformers.AutoModelForMaskedLM) - Language modeling Head
2. [AutoModelForSequenceClassification](https://huggingface.co/docs/transformers/model_doc/auto#transformers.AutoModelForSequenceClassification) - Classification Head
3. [AutoModelForTokenClassification](https://huggingface.co/docs/transformers/model_doc/auto#transformers.AutoModelForTokenClassification) - Token Classification Head

Feel free to read the [documentation](https://huggingface.co/docs/transformers/model_doc/auto#auto-classes) for a list of other possible heads

In [44]:
# Load in the bert-base-cased model with a classification head (num_labels = number of classes)
classification_head_bert = AutoModelForSequenceClassification.from_pretrained("bert-base-cased", num_labels=5)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


### **Training the Model + Classification head**

Let's now train the model + classification head for sentiment analysis. We will use the HuggingFace [Trainer](https://huggingface.co/docs/transformers/main_classes/trainer) class. We need to:
1. Tokenize and process the dataset
2. Create a `compute_metrics` function
3. Initialize the `Trainer` and specify the `TrainingArguments`

### **Step 1: Tokenize and Process the dataset**

For this section you must implement the `tokenize_function`. This function should run the BERT tokenizer on every example in the dataset and add the output fields `input_ids`, `attention_mask`, and `token_type_ids` as new columns in the dataset.

This function should also also pad all sequences of less than 512 tokens to be exactly 512 tokens using the special `[PAD]` token and truncate sequences longer than 512 to be exactly 512. This is to help GPU parallelization and can be done by specifying certain arguments to the tokenizer (check the [documentation](https://huggingface.co/docs/transformers/v4.30.0/en/main_classes/tokenizer#transformers.PreTrainedTokenizer.__call__)!)

In [50]:
# Step 1: Tokenize and Process the dataset
dataset = load_dataset("yelp_review_full")
tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")

def tokenize_function(row):
  # Tokenize the dataset (Remember to pad and truncate to max length)
  ## YOUR CODE STARTS HERE ###
  ### perform tokenization on the dataset to add padd and truncation
  token_out=tokenizer(row['text'], padding='max_length',
                      truncation=True,max_length=512) ### load the tokenizer
  row['input_ids']=token_out['input_ids'] # tokenize every thing here
  row['attention_mask']=token_out['attention_mask']
  row['token_type_ids']=token_out['token_type_ids']

  # row['label']=torch.tensor(row['label'])
  ### YOUR CODE ENDS HERE ###
  return row

# Randomly select 1000 examples from the train and test data and tokenize - do not change!
# (Note: We are subsampling our data just so that training doesn't take too long)
train_data = dataset["train"].shuffle(seed=42).select(range(1000)).map(tokenize_function)
eval_data = dataset["test"].shuffle(seed=42).select(range(1000)).map(tokenize_function)

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

In [51]:
print(train_data[:500])

{'label': [4, 2, 4, 0, 2, 2, 3, 0, 0, 4, 0, 4, 3, 1, 3, 0, 4, 3, 4, 2, 0, 4, 0, 1, 0, 1, 1, 2, 4, 3, 3, 2, 4, 3, 0, 2, 2, 0, 1, 2, 2, 2, 0, 1, 4, 1, 1, 2, 0, 2, 1, 1, 2, 4, 1, 3, 2, 4, 3, 3, 3, 1, 0, 3, 3, 2, 1, 0, 0, 0, 3, 2, 0, 3, 4, 4, 0, 1, 3, 1, 0, 3, 1, 4, 1, 3, 2, 3, 2, 4, 3, 3, 1, 4, 0, 2, 4, 1, 4, 3, 3, 3, 0, 2, 4, 0, 4, 4, 2, 1, 4, 3, 4, 1, 2, 0, 3, 0, 0, 0, 4, 3, 1, 0, 3, 4, 0, 4, 1, 4, 0, 3, 0, 1, 2, 3, 0, 1, 2, 2, 2, 1, 0, 2, 3, 4, 2, 0, 1, 1, 3, 1, 1, 0, 3, 2, 4, 3, 3, 4, 4, 0, 2, 3, 4, 1, 1, 4, 3, 2, 1, 1, 3, 3, 4, 3, 1, 0, 4, 2, 1, 4, 3, 4, 1, 0, 0, 1, 4, 4, 3, 2, 0, 2, 3, 0, 3, 1, 3, 4, 1, 1, 2, 2, 2, 2, 3, 0, 0, 2, 3, 3, 3, 3, 4, 3, 0, 3, 4, 3, 3, 1, 4, 0, 0, 2, 3, 3, 4, 0, 4, 4, 4, 0, 2, 1, 2, 0, 2, 3, 4, 3, 1, 1, 4, 0, 1, 3, 1, 0, 3, 1, 2, 1, 3, 0, 2, 4, 3, 3, 0, 3, 2, 4, 0, 0, 1, 0, 3, 2, 1, 4, 4, 4, 2, 0, 2, 1, 2, 3, 0, 3, 1, 0, 1, 4, 2, 1, 2, 4, 3, 4, 4, 1, 2, 1, 0, 0, 4, 3, 2, 3, 1, 1, 4, 0, 1, 3, 0, 3, 1, 3, 4, 3, 2, 1, 2, 2, 3, 3, 3, 0, 2, 2, 2, 4, 2, 2, 3, 3,

### **Step 2: Define a `compute_metrics` function**

For this function you'll be calculating accuracy between the predictions and true labels. The `probabilities` variable is a 2D numpy array of size ($n$ x $5$) containing probabilities for the 5 class labels for each of the $n$ examples in the input dataset.

You must write code to select the index with the highest probability for each row in the `probabilities` array then calculate the accuracy of the model with respect to the ground truth label. (HINT: the [np.argmax](https://numpy.org/doc/stable/reference/generated/numpy.argmax.html) function is really nice for this)

In [53]:
# Step 2: Define a compute_metrics function
def compute_metrics(eval_pred):
    # Get the true labels and predicted probabilities
    probabilities, labels = eval_pred

    #compute accuracy between predictions & true labels
    ### YOUR CODE STARTS HERE ###
    pred=np.argmax(probabilities,axis=1)
    acc=accuracy(pred,labels)
    ### YOUR CODE ENDS HERE

    return {'accuracy': acc}

### **Step 3: Initialize the `Trainer` and Specify `TrainingArguments`**

Here we specify various arguments to the trainer. We choose to evaluate and log every `epoch` (i.e. every pass through the full dataset), we specify the output directory for checkpoints, the learning rate (`5e-05`), the number of epochs (`3`), and the size of batches used for stochastic gradient descent (`8`). In addition, we specify full_determinism for the sake of grading consistency.

In the Trainer we specify our model as the BERT model we loaded earlier, we pass in our argument and filtered datasets, and finally we pass in our `compute_metrics` function.

In [54]:
# Step 3: Specify the TrainingArguments and Initialize the Trainer (Do not change!)
training_args = TrainingArguments(
    evaluation_strategy="epoch",
    logging_strategy="epoch",
    output_dir="yelp-training",
    learning_rate=5e-05,
    num_train_epochs=3.0,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    full_determinism=True,
    report_to="none"
)

trainer = Trainer(
    model=classification_head_bert,
    args=training_args,
    train_dataset=train_data,
    eval_dataset=eval_data,
    compute_metrics=compute_metrics,
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1568: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


### **Time to Train!**

Once all the above cells have finished running it is time to train the model. On GPU this should only take about 5 minutes.

In [55]:
# Train the model!
trainer.train()
trainer.save_model('./yelpBERT')

## Sanity-Checking our trained model

In order to run our trained model we need to load it into a `text-classification` pipeline. A quick sanity check should show us that our model outputs sensible results

In [56]:
yelpBERT = pipeline('text-classification', model='./yelpBERT', tokenizer=tokenizer, device=device_id)

In [57]:
# Output sentiment for reviews (LABEL_4 = 5 stars, LABEL_0 = 1 star)
yelpBERT(["This place was amazing!",
          "This place was good",
          "This place was fine, there were good and bad parts.",
          "This place was pretty bad",
          "This place was awful"])

[{'label': 'LABEL_4', 'score': 0.880397617816925},
 {'label': 'LABEL_3', 'score': 0.7725221514701843},
 {'label': 'LABEL_2', 'score': 0.736090898513794},
 {'label': 'LABEL_1', 'score': 0.7264488935470581},
 {'label': 'LABEL_0', 'score': 0.870612382888794}]

## Evaluating the model

In order to get the official evaluation results we will be using the [Evaluator](https://huggingface.co/docs/evaluate/v0.4.0/en/package_reference/evaluator_classes#evaluator) pipeline for a standardized evaluation environment. Please run the following code to get the accuracy of your model on the Yelp dataset. We will be grading your model's accuracy. Your model should be at least higher than 55% to recieve full credit for this section.

In [58]:
task_evaluator = evaluator("text-classification")

eval_results = task_evaluator.compute(
    model_or_pipeline=yelpBERT,
    data=eval_data,
    metric=evaluate.load("accuracy"),
    label_mapping={"LABEL_0": 0, "LABEL_1": 1, "LABEL_2": 2, "LABEL_3": 3, "LABEL_4": 4}
)

print(eval_results)

{'accuracy': 0.585, 'total_time_in_seconds': 25.334039990000292, 'samples_per_second': 39.47258314878773, 'latency_in_seconds': 0.025334039990000293}


# Part 3: Training BERT for Natural Language Inference

In this section you will train BERT to perform a new task -- Natural Language Inference (NLI). NLI is the task of taking two pieces of text (a "premise" and "hypothesis") and determining whether or not the premise is entailed from the hypothesis.


> Natural Language Inference is a task of determining whether the given “hypothesis” and “premise” logically follow (entailment) or unfollow (contradiction) or are undetermined (neutral) to each other. ~ [Oleh Loksyn](https://towardsdatascience.com/natural-language-inference-an-overview-57c0eecf6517)

This can be formulated as a sequence classification task where, given both sequences, we predict one of three labels

(0 = contradiction, 1 = neutral, 2 = entailment)

### **Applying BERT to multiple sequences**

In order to encode multiple sequences of non-contiguous text with BERT we use the `[SEP]` token. This token is a special token (similar to `[MASK]`) that indicates to the model that the sequences on either side of the token are distinct. With the `[SEP]` token we're able to concatenate the premise and hypothesis together into one sequence allowing us to use a standard classification head.

### **Loading BERT**
Your first task is to load in BERT with a classification head. This should be identical to the loading code from Section 2 save for a different number of labels

In [59]:
#Load in the bert-base-cased model with a classification head (remember the right number of labels!)
### YOUR CODE STARTS HERE ###
classification_head_bert = AutoModelForSequenceClassification.from_pretrained("bert-base-cased", num_labels=3)
### YOUR CODE ENDS HERE ###

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


### **The MNLI Dataset**
For this task we'll be using the [Multi-Genre NLI](https://huggingface.co/datasets/multi_nli) dataset. This dataset was collected by asking crowd workers to annotate 433,000 sentence pairs from various genres (Fiction, Travel, Telephone, Letters, Government) for their textual entailment information.

In [60]:
mnli = load_dataset("multi_nli")

README.md:   0%|          | 0.00/8.89k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/214M [00:00<?, ?B/s]

(…)alidation_matched-00000-of-00001.parquet:   0%|          | 0.00/4.94M [00:00<?, ?B/s]

(…)dation_mismatched-00000-of-00001.parquet:   0%|          | 0.00/5.10M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/392702 [00:00<?, ? examples/s]

Generating validation_matched split:   0%|          | 0/9815 [00:00<?, ? examples/s]

Generating validation_mismatched split:   0%|          | 0/9832 [00:00<?, ? examples/s]

### **Tokenize and Process the Dataset**
In this section you must implement the three processing functions `is_labeled`, `concatenate` and `tokenize_function`. These should be fairly similar to the processing functions we've been dealing with so far.

In [61]:
def is_labeled(row):
  # Filter out all examples that do not have an entailment label (i.e. label is -1)
  ### YOUR CODE STARTS HERE ###
  if row['label']==-1:
    return False
  return True
  ### YOUR CODE ENDS HERE ###

mnli = mnli.filter(is_labeled)

Filter:   0%|          | 0/392702 [00:00<?, ? examples/s]

Filter:   0%|          | 0/9815 [00:00<?, ? examples/s]

Filter:   0%|          | 0/9832 [00:00<?, ? examples/s]

In [62]:
def concatenate(row):
  #      　Concatenate the text of the "premise" column to the "hypothesis" column
  #        using the [SEP] token. Must be in the order "<premise> [SEP] <hypothesis>"
  #        Add the output as a new column "concat" to the dataset
  ### YOUR CODE STARTS HERE ###
  row['concat']=row['premise']  + ' [SEP] ' +  row['hypothesis']
  ### YOUR CODE ENDS HERE ###
  return row

mnli = mnli.map(concatenate)

Map:   0%|          | 0/392702 [00:00<?, ? examples/s]

Map:   0%|          | 0/9815 [00:00<?, ? examples/s]

Map:   0%|          | 0/9832 [00:00<?, ? examples/s]

In [63]:
tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")

def tokenize_function(row):
  # tokenize the concatenated data (make sure to pad and truncate to max length!)
  ### YOUR CODE STARTS HERE ###
  token_out=tokenizer(row['concat'], padding='max_length',
                      truncation=True,max_length=512)
  row['input_ids']=token_out['input_ids']
  row['attention_mask']=token_out['attention_mask']
  row['token_type_ids']=token_out['token_type_ids']
  ### YOUR CODE ENDS HERE ###
  return row

# Randomly select 1000 examples from train and validation and process them (Do not change!)
train_mnli = mnli["train"].shuffle(seed=42).select(range(1000)).map(tokenize_function)
eval_mnli = mnli["validation_matched"].shuffle(seed=42).select(range(1000)).map(tokenize_function)

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

In [64]:
print(train_mnli[:500])

{'promptID': [24261, 87764, 22801, 104314, 103591, 121253, 75824, 53570, 34884, 117513, 118869, 99511, 15122, 90085, 144312, 101956, 98534, 15357, 16727, 143652, 22396, 109548, 48245, 19835, 105860, 110522, 65314, 54153, 134376, 128470, 116072, 106944, 22302, 41755, 62245, 135237, 97397, 56449, 143189, 142866, 114870, 19918, 52983, 134329, 106799, 116769, 45121, 7113, 90384, 51169, 91342, 119018, 83834, 70543, 94868, 64442, 18228, 17374, 91699, 47110, 37356, 126085, 16634, 67721, 49927, 115649, 25780, 136069, 52812, 10132, 10826, 73776, 96256, 120531, 75056, 105387, 9727, 66661, 8931, 140518, 123646, 33285, 92907, 85886, 75464, 117330, 138842, 107652, 135970, 110742, 50459, 62972, 97408, 91536, 103670, 34440, 108117, 129975, 35617, 145324, 12245, 76063, 16254, 63306, 3384, 82839, 106243, 36996, 117875, 106121, 117877, 7520, 54482, 68831, 92487, 9460, 102394, 57362, 36752, 98264, 27570, 5021, 52565, 4336, 105629, 60205, 108798, 53454, 125908, 11369, 43177, 31177, 92467, 49457, 41900, 10

### **Define the `compute_metrics` function**
For this section you'll define the compute_metrics function. We'll be using accuracy again in this section. Feel free to reference your implementation from the previous section to help you out.

In [65]:
def compute_metrics(eval_pred):
    # extract the outputs of the model and compute accuracy
    ### YOUR CODE STARTS HERE ###
    probabilities, labels = eval_pred
    pred=np.argmax(probabilities,axis=1)
    acc=accuracy(pred,labels)
    ### YOUR CODE ENDS HERE ###
    return {"accuracy": None}

### **Initialize the `TrainingArguments` and `Trainer`**

In [66]:
training_args = TrainingArguments(
    evaluation_strategy="epoch",
    logging_strategy="epoch",
    output_dir="mnli-training",
    learning_rate=5e-05,
    num_train_epochs=3.0,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    full_determinism=True,
    report_to="none"
)

trainer = Trainer(
    model=classification_head_bert,
    args=training_args,
    train_dataset=train_mnli,
    eval_dataset=eval_mnli,
    compute_metrics=compute_metrics,
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1568: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


### **Train the model**

In [67]:
trainer.train()
trainer.save_model('./mnliBERT')

### **Sanity Check**

Once again, if trained properly, a quick sanity check should provide us with sensible results

In [68]:
mnliBERT = pipeline('text-classification', model='./mnliBERT', tokenizer=tokenizer, device=device_id)

In [69]:
# Output entailment (LABEL_0 = entailment, LABEL_1 = neutral, LABEL_2 = contradiction)
mnliBERT(["I just graduated college. [SEP] The person is a college graduate.",
          "My name is John. [SEP] The sky is blue.",
          "Thank you so much for your help. [SEP] The person was not helped."])

[{'label': 'LABEL_1', 'score': 0.9395487904548645},
 {'label': 'LABEL_1', 'score': 0.9481647610664368},
 {'label': 'LABEL_2', 'score': 0.962492048740387}]

### **Evaluate the Model**

Please run the following code to evaluate your model on the MNLI dataset. Your model should be at least 55% accurate to receive full credit.

In [70]:
task_evaluator = evaluator("text-classification")

eval_results = task_evaluator.compute(
    model_or_pipeline=mnliBERT,
    data=eval_mnli,
    input_column="concat",
    label_column="label",
    metric=evaluate.load("accuracy"),
    label_mapping={"LABEL_0": 0, "LABEL_1": 1, "LABEL_2": 2}
)

print(eval_results)

{'accuracy': 0.55, 'total_time_in_seconds': 25.822636296999917, 'samples_per_second': 38.72571291708819, 'latency_in_seconds': 0.025822636296999917}


In [71]:
print(eval_results)

{'accuracy': 0.55, 'total_time_in_seconds': 25.822636296999917, 'samples_per_second': 38.72571291708819, 'latency_in_seconds': 0.025822636296999917}


# Part4 : Training BERT for Named-Entity Recognition

In this final section you will train BERT to perform [Named Entity Recognition](https://en.wikipedia.org/wiki/Named-entity_recognition) (NER).

NER is the task of tagging and identifying named entities (e.g. People, Organizations, Locations) in text. For example the sentence "Only France and Britain backed Fischler's proposal." would be tagged as

> Only (France, LOC) and (Britain, LOC) backed (Fischler's, PER) proposal.

NER is typically formulated as a token classification task. Given a sequence of tokens we assign a class to each token. Tokens that are not named entities get given the null tag `O` and tokens that are named entities get one of four classes (`ORG`, `PER`, `LOC`, or `MISC`). Thus the sentence from earlier would be given the labels

>(Only, O) (France, LOC) (and, O) (Britain, LOC) (backed, O) (Fischler's, PER) (proposal, O)

Giving every token in the sequence a label allows us to use a token classification head for this task.

### **Beginning-Inside-Outside (BIO) tags**

One downside to the tagging scheme described is that for two consecutive tokens with the same tag, we can't tell whether or not they are the same entity. For example

> ("25-1", 0), ("Barcelona", ORG), ("Real", ORG), ("Madrid", ORG)

We know that [Real Madrid](https://en.wikipedia.org/wiki/Real_Madrid_CF) and [Barcelona](https://en.wikipedia.org/wiki/FC_Barcelona) are distinct entities but our tag system combines them together. Thus we must distinguish between tags that *begin* an entity (`B-ORG`) and those that are *inside* an entity (`I-ORG`). With this new system we get

> ("25-1", O), ("Barcelona", B-ORG), ("Real", B-ORG), ("Madrid", I-ORG)

Which allows us to distinguish between the two consecutive entities.

### **Training BERT + Token Classification Head**

In order to train BERT for NER we need to use a token classification head. Token classification heads are dense linear layers that output a probability distribution over $n$ classes *for each token* in the sequence. This is equivalent to having $L_{context}$ different classification heads, each trained to predict an output at a specific index. The total size of a token classification head is ($L_{context} * D_{enc}$ x $n * L_{context}$).

### **Load the Model**
Your first task is to load BERT with a token classification head. Take care that the `num_labels` and `id2label` parameters are set correctly.

HINT: Refer back to Section 2's discussion of model heads to find mention (and documentation) for the token classification head class.

In [72]:
label_names = {0: 'O', 1: 'B-PER', 2: 'I-PER', 3: 'B-ORG', 4: 'I-ORG', 5: 'B-LOC', 6: 'I-LOC', 7: 'B-MISC', 8:'I-MISC'}
#Load the model with the right num_labels and set id2label to be label_names
### YOUR CODE STARTS HERE ###

token_classification_head_bert = AutoModelForTokenClassification.from_pretrained("bert-base-cased", num_labels=len(label_names), id2label=label_names)

### YOUR CODE ENDS HERE ###

Some weights of BertForTokenClassification were not initialized from the model checkpoint at bert-base-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [73]:
attributes = copy.deepcopy(vars(token_classification_head_bert))
attributes['config'] = attributes['config'].__dict__
del attributes['_modules']

### **The CoNLL Dataset**

We will use the [CoNLL](https://huggingface.co/datasets/conll2003) dataset as our training data for NER. This dataset consists of 20,000 sentences from Reuters news articles that were manually annotated by participants for their named entities. The tags used are the four classes from earlier (`ORG`, `PER`, `LOC`, or `MISC`) with both `B-` and `I-` variants as well as a null tag `O`.

In [75]:
conll = load_dataset("conll2003")

README.md:   0%|          | 0.00/12.3k [00:00<?, ?B/s]

conll2003.py:   0%|          | 0.00/9.57k [00:00<?, ?B/s]

The repository for conll2003 contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/conll2003.
You can avoid this prompt in future by passing the argument `trust_remote_code=True`.

Do you wish to run the custom code? [y/N] y


Generating train split:   0%|          | 0/14041 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/3250 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/3453 [00:00<?, ? examples/s]

### **Token-tag mismatch**
When processing data for a tagging task, we need to ensure that the tags properly match up to all the correct tokens. BERT's tokenizer is a [Byte-Pair Encoding](https://en.wikipedia.org/wiki/Byte_pair_encoding) (BPE) tokenizer that tends to split up words into sub-word tokens. For example, take the sentence from earlier
> "Only France and Britain backed Fischler's proposal"

We can see below that the tokenization from CoNLL doesn't match the BERT tokenizer. This creates a problem when processing the tags, as we need to keep the correspondence between tags and tokens. It will be up to you to fix this

In [76]:
print(conll['train'][12]['ner_tags'])
print(tokenizer.convert_ids_to_tokens(tokenizer.encode("Only France and Britain backed Fischler's proposal"))[1:-1])

[0, 5, 0, 5, 0, 1, 0, 0, 0]
['Only', 'France', 'and', 'Britain', 'backed', 'Fi', '##sch', '##ler', "'", 's', 'proposal']


### **Redistributing Tags to Sub-word Tokens**
Your job is to implement the `tokenize_and_tag` function. This function should do three things
1. Retokenize the tokens from CoNLL using the BERT tokenizer and add the outputs (`input_ids`, `attention_mask`, and `token_type_ids`) as new columns in the dataset.
2. Redistribute the NER tags with respect to the newly tokenized sequence and add the tags as a new `labels` column to the dataset
3. Pad and truncate both the tokens and tags to be length `tokenizer.model_max_length` (512)

If a token is broken up into multiple sub-tokens then all sub-tokens should be given the same NER tag as the original token.

Some example inputs and outputs are as follows (Reminder to consult the `label_names` dictionary for the mapping from number to NER tag):
```
-- Example #1 --
Inputs:
"tokens": ['John', 'Smith', 'works', 'at', 'Google', 'in', 'Mountain', 'View', ',', 'California', '.']
"ner_tags": [1, 1, 0, 0, 2, 0, 5, 5, 0, 5, 0]

Outputs:
"bert_tokens": ['[CLS]', 'john', 'smith', 'works', 'at', 'google', 'in', 'mountain', 'view', ',', 'california', '.', '[SEP]', '[PAD]', '[PAD]', ...]
"input_ids": [101, 2198, 2047, 2147, 2012, 2345, 1999, 2661, 2175, 1010, 2149, 1012, 102, 0, 0, ...]
"labels": [-100, 1, 1, 0, 0, 2, 0, 5, 5, 0, 5, 0, -100, -100, -100, ...]

-- Example #2 --
Inputs:
"tokens": ['66', 'Paul', 'Goydos', ',', 'Billy', 'Mayfair', ',', 'Hidemichi', 'Tanaka', '(', 'Japan', ')']
"ner_tags": [0, 1, 2, 0, 1, 2, 0, 1, 2, 0, 5, 0]

Outputs:
"bert_tokens": ['[CLS]', '66', 'Paul', 'Go', '##yd', '##os', ',', 'Billy', 'May', '##fair', ',', 'Hi', '##de', '##mic', '##hi', 'Tanaka', '(', 'Japan', ')', '[SEP]', '[PAD]', '[PAD]', ...]
"input_ids": [101, 5046, 1795, 3414, 19429, 2155, 117, 4224, 1318, 19803, 117, 8790, 2007, 7257, 3031, 24128, 113, 1999, 114, 102, 0, 0, ...]
"labels": [-100, 0, 1, 2, 2, 2, 0, 1, 2, 2, 0, 1, 1, 1, 1, 2, 0, 5, 0, -100, -100, -100, ...]
```
**NOTE:** Make sure to use the label `-100` for all special tokens (`[CLS]`, `[SEP]`, `[PAD]`). Using this label will ensure that special tokens will be ignored by PyTorch and will not contribute to the loss calculation.

In [79]:
def tokenize_and_tag(row):

  # Redistribute and tokenize the CoNLL dataset using the BERT tokenizer
  ### YOUR CODE STARTS HERE ###
  tokenized= tokenizer(row['tokens'], is_split_into_words=True, truncation=True,padding='max_length', max_length=tokenizer.model_max_length)
  word_ID= tokenized.word_ids()
  tokenLabel=[]
  for word_id in word_ID:
    if word_id == None:
      tokenLabel.append(-100) # -100 is the labe; for special tokens
    else:
      tokenLabel.append(row['ner_tags'][word_id])
  row['labels']=tokenLabel
  row['input_ids']=tokenized['input_ids']
  row['attention_mask']=tokenized['attention_mask']
  ### YOUR CODE ENDS HERE ###
  return row

# randomly select 1000 examples from train and validation and call tokenize_and_tag
### YOUR CODE STARTS HERE ###
train_conll = conll["train"].shuffle(seed=42).select(range(1000)).map(tokenize_and_tag)
eval_conll = conll["validation"].shuffle(seed=42).select(range(1000)).map(tokenize_and_tag)
### YOUR CODE ENDS HERE ###

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

In [80]:
print(conll["train"].select(range(350)).map(tokenize_and_tag)[:])

Map:   0%|          | 0/350 [00:00<?, ? examples/s]

{'id': ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21', '22', '23', '24', '25', '26', '27', '28', '29', '30', '31', '32', '33', '34', '35', '36', '37', '38', '39', '40', '41', '42', '43', '44', '45', '46', '47', '48', '49', '50', '51', '52', '53', '54', '55', '56', '57', '58', '59', '60', '61', '62', '63', '64', '65', '66', '67', '68', '69', '70', '71', '72', '73', '74', '75', '76', '77', '78', '79', '80', '81', '82', '83', '84', '85', '86', '87', '88', '89', '90', '91', '92', '93', '94', '95', '96', '97', '98', '99', '100', '101', '102', '103', '104', '105', '106', '107', '108', '109', '110', '111', '112', '113', '114', '115', '116', '117', '118', '119', '120', '121', '122', '123', '124', '125', '126', '127', '128', '129', '130', '131', '132', '133', '134', '135', '136', '137', '138', '139', '140', '141', '142', '143', '144', '145', '146', '147', '148', '149', '150', '151', '152', '153', '154', '155', '156', '15

### **Computing Macro-Averaged F1 Score**

We want to compute the accuracy of our model when identifying named entities. However, most sequences consist mostly of `O` tags. This is bad for our evaluation, as it means that predicting a sequence of all `O`s will result in high accuracy despite not actually accomplishing the task.

To solve this problem we will be using the Macro-Averaged F1 Score as our metric. This is the unweighted average of the F1 scores for each individual token class. This is a common metric to use when given an unbalanced multi-class classification task. Feel free to read [this article](https://stephenallwright.com/micro-vs-macro-f1-score/) for a full explanation of Macro-F1 as it will be useful for your implementation.

You are to implement the `calculate_macro_f1` function. This function should:
1. Calculate the full confusion matrix (TP, TN, FP, FN) for each class
2. Compute the precision, recall, and f1 score for each class
3. Macro-Average together the F1 score for all nine classes to get the final score

**NOTE**: Typically for NER a correct entity prediction is considered to be one that exactly matches all `B-` and `I-` tags. However, to make the Macro-F1 calculation easier we are considering all of our nine different tag classes as fully separate.

**TIP**: You can use the [sklearn.metrics.f1_score](https://scikit-learn.org/stable/modules/generated/sklearn.metrics.f1_score.html) function from scikitlearn to check your implementation. To help debug we have provided the handy `debug_macro_f1` function for you to use. This function generates random test cases and compares the output of your implementation to that of scikitlearn's. If the two do not match it prints out the failed example. This should be helpful when debugging.

In [103]:
def calculate_macro_f1(preds, labels):
  # Filter out -100 and convert ids to tags
  label_map = {0: 'O', 1: 'B-PER', 2: 'I-PER', 3: 'B-ORG', 4: 'I-ORG', 5: 'B-LOC', 6: 'I-LOC', 7: 'B-MISC', 8:'I-MISC'}
  true_preds = [
      [(label_map[p], label_map[l]) for (p, l) in zip(pred, label) if l in label_map]
      for pred, label in zip(preds, labels)
  ]

  # Compute confusion matrices for each class
  # Compute precision, recall, and f1 for each class
  # Macro-Average them together

  ### YOUR CODE STARTS HERE ###
  num_classes=len(label_map)
  pred_flatten = []
  labels_flatten=[]
  for predictions,labels in zip(preds,labels):
    for prediction, label in zip(predictions,labels):
      if label!=-100: ## i ams skipping the pads
        pred_flatten.append(prediction)
        labels_flatten.append(label)

  true_p =np.zeros(num_classes)
  false_p =np.zeros(num_classes)
  false_n =np.zeros(num_classes)

  for pred, label in zip(pred_flatten, labels_flatten):
    if pred==label:
      true_p[label]+=1
    elif pred!=label and label!=0:
      false_p[pred]+=1
      false_n[label]+=1

  f1_scores=[]
  for i in range(num_classes):
      precision=true_p[i]/(true_p[i]+false_p[i]) if (true_p[i]+false_p[i]) > 0 else 0.0
      recall=true_p[i]/(true_p[i]+false_n[i]) if (true_p[i]+false_n[i]) > 0 else 0.0
      f1=2*precision*recall/(precision+recall) if (precision+recall) > 0 else 0.0
      f1_scores.append(f1)
  macrof1=np.mean(f1_scores)

  ### YOUR CODE ENDS HERE ###

  return {"macro-f1": macrof1}

In [104]:
from sklearn.metrics import f1_score

def debug_macro_f1(num_tests, len_examples):
  # For each random test case
  for i in range(num_tests):
    # Generate two random arrays for the predictions and labels
    rand_preds = np.random.randint(0,9,len_examples).tolist()
    rand_labels = np.random.randint(0,9,len_examples).tolist()

    # Calculate Macro-F1 score with your implementation and scikitlearn
    sklearn_f1 = f1_score(rand_labels, rand_preds, average='macro')
    your_f1 = calculate_macro_f1([rand_preds], [rand_labels])

    # If the two implementations differ, print the example and the scores
    if abs(sklearn_f1 - your_f1['macro-f1']) <= 0.001:
      print(f'preds: {rand_preds}')
      print(f'labels: {rand_labels}')
      print(sklearn_f1, your_f1['macro-f1'])

debug_macro_f1(1, 10)

preds: [6, 3, 7, 4, 6, 2, 6, 7, 4, 3]
labels: [7, 7, 2, 5, 4, 1, 7, 5, 1, 4]
0.0 0.0


In [105]:
def compute_metrics(eval_pred):
  logits, labels = eval_pred
  preds = np.argmax(logits, axis=2)
  return calculate_macro_f1(preds, labels)

### **Training the model**

In [106]:
training_args = TrainingArguments(
    evaluation_strategy="epoch",
    logging_strategy="epoch",
    output_dir="conll-training",
    learning_rate=5e-05,
    num_train_epochs=3.0,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    full_determinism=True,
    report_to="none"
)


trainer = Trainer(
    model=token_classification_head_bert,
    args=training_args,
    train_dataset=train_conll,
    eval_dataset=eval_conll,
    compute_metrics=compute_metrics
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1568: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [107]:
trainer.train()
trainer.save_model('./nerBERT')

### **Sanity Checking the NER Predictions**
In order to check our model we need to load it into a `token-classification` pipeline.

If your model has been trained correctly then you will see in the following example that it correctly predicts the "Pennsylvania" in "University of Pennsylvania" as an `ORG` but "Philadelphia" as a `LOC`.

In [98]:
nerBERT = pipeline('token-classification', model='./nerBERT', tokenizer=tokenizer, device=device_id)

In [99]:
nerBERT(["Chris Callison-Burch is a professor at the University of Pennsylvania in Philadelphia",
          "Joe Biden is the 46th President of the United States"], aggregation_strategy="simple")

[[{'entity_group': 'PER',
   'score': 0.9971908,
   'word': 'Chris Callison - Burch',
   'start': 0,
   'end': 20},
  {'entity_group': 'ORG',
   'score': 0.7237608,
   'word': 'University of Pennsylvania',
   'start': 43,
   'end': 69},
  {'entity_group': 'LOC',
   'score': 0.99704224,
   'word': 'Philadelphia',
   'start': 73,
   'end': 85}],
 [{'entity_group': 'PER',
   'score': 0.9989353,
   'word': 'Joe Biden',
   'start': 0,
   'end': 9},
  {'entity_group': 'LOC',
   'score': 0.9968214,
   'word': 'United States',
   'start': 39,
   'end': 52}]]

### **Evaluating NER with SeqEval**

The official library for evaluating a model on the CoNLL task is [SeqEval](https://github.com/chakki-works/seqeval). We'll be downloading it and using it to officially score our model. The SeqEval `overall_f1` is identical to your Macro-F1 implementation with the slight caveat that it uses the traditional NER definition of a correct tag prediction (i.e. one that exactly matches all `B-` and `I-` tags). Thus, don't worry if the official result doesn't match your macro-f1 implementation.

For this task, in order to receive full credit, your implementation must get a Macro-F1 score of at least 0.82.

In [100]:
!pip install seqeval

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 1.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for seqeval: filename=seqeval-1.2.2-py3-none-any.whl size=16161 sha256=e14fe32eedef62503aa3288e0054068b640cb9d56d88031cb5ce4b30dfc29d01
  Stored in directory: /root/.cache/pip/wheels/1a/67/4a/ad4082dd7dfc30f2abfe4d80a2ed5926a506eb8a972b4767fa
Successfully built seqeval


In [101]:
task_evaluator = evaluator("token-classification")

eval_results = task_evaluator.compute(
    model_or_pipeline=nerBERT,
    data=eval_conll,
    input_column="tokens",
    label_column="ner_tags",
    tokenizer=tokenizer,
    metric=evaluate.load("seqeval")
)

for key in eval_results:
  print(f"{key}: {eval_results[key]}")

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

LOC: {'precision': 0.9318181818181818, 'recall': 0.9253472222222222, 'f1': 0.9285714285714286, 'number': 576}
MISC: {'precision': 0.7459807073954984, 'recall': 0.8226950354609929, 'f1': 0.7824620573355817, 'number': 282}
ORG: {'precision': 0.8188775510204082, 'recall': 0.8469656992084432, 'f1': 0.8326848249027238, 'number': 379}
PER: {'precision': 0.9660107334525939, 'recall': 0.9694793536804309, 'f1': 0.9677419354838709, 'number': 557}
overall_precision: 0.8865866957470011
overall_recall: 0.9063545150501672
overall_f1: 0.896361631753032
overall_accuracy: 0.9825386597938144
total_time_in_seconds: 55.882782025999404
samples_per_second: 17.89459944092889
latency_in_seconds: 0.05588278202599941


In [102]:
print(eval_results)

{'LOC': {'precision': 0.9318181818181818, 'recall': 0.9253472222222222, 'f1': 0.9285714285714286, 'number': 576}, 'MISC': {'precision': 0.7459807073954984, 'recall': 0.8226950354609929, 'f1': 0.7824620573355817, 'number': 282}, 'ORG': {'precision': 0.8188775510204082, 'recall': 0.8469656992084432, 'f1': 0.8326848249027238, 'number': 379}, 'PER': {'precision': 0.9660107334525939, 'recall': 0.9694793536804309, 'f1': 0.9677419354838709, 'number': 557}, 'overall_precision': 0.8865866957470011, 'overall_recall': 0.9063545150501672, 'overall_f1': 0.896361631753032, 'overall_accuracy': 0.9825386597938144, 'total_time_in_seconds': 55.882782025999404, 'samples_per_second': 17.89459944092889, 'latency_in_seconds': 0.05588278202599941}
